In [1]:
from pyspark import SparkContext, SparkConf
cf = SparkConf()
cf.set("spark.submit.deployMode","client")
sc = SparkContext.getOrCreate(cf)
from pyspark.sql import SparkSession
spark = SparkSession \
	    .builder \
	    .appName("TransitTrends- Taxi") \
	    .config("spark.some.config.option", "some-value") \
	    .getOrCreate()

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/04/21 23:55:49 INFO org.apache.spark.SparkEnv: Registering MapOutputTracker
23/04/21 23:55:49 INFO org.apache.spark.SparkEnv: Registering BlockManagerMaster
23/04/21 23:55:49 INFO org.apache.spark.SparkEnv: Registering BlockManagerMasterHeartbeat
23/04/21 23:55:49 INFO org.apache.spark.SparkEnv: Registering OutputCommitCoordinator


In [2]:
import os
from sodapy import Socrata
import pandas as pd
import numpy as np

In [3]:
### Loading All datasets

In [4]:
import subprocess
# downloading Yellow cab data(2019-2022) from site https://www.nyc.gov/site/tlc/about/tlc-trip-record-data.page
url = "https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_20"
output_dir = "/home/sk9944_nyu_edu/TAXI/YELLOW_CABS/"
for i in range(19,23):
    for j in range(1, 13):
        url_1 = str(j)
        if j<10:
            url_1 = "0"+url_1
        print("wget "+ url+str(i)+"-"+url_1+".parquet")
        # Run wget command
        subprocess.call(["wget", "-P", output_dir, url+str(i)+"-"+url_1+".parquet"])

wget https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2019-01.parquet


--2023-04-21 23:56:37--  https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2019-01.parquet
Resolving d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)... 54.230.209.140, 54.230.209.200, 54.230.209.72, ...
Connecting to d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)|54.230.209.140|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 110439634 (105M) [application/x-www-form-urlencoded]
Saving to: ‘/home/sk9944_nyu_edu/TAXI/YELLOW_CABS/yellow_tripdata_2019-01.parquet’

     0K .......... .......... .......... .......... ..........  0% 5.51M 19s
    50K .......... .......... .......... .......... ..........  0% 4.23M 22s
   100K .......... .......... .......... .......... ..........  0% 14.1M 17s
   150K .......... .......... .......... .......... ..........  0% 9.14M 16s
   200K .......... .......... .......... .......... ..........  0% 14.8M 14s
   250K .......... .......... .......... .......... ..........  0% 16.0M 13s
   30

 25150K .......... .......... .......... .......... .......... 23% 83.2M 1s
 25200K .......... .......... .......... .......... .......... 23% 82.1M 1s
 25250K .......... .......... .......... .......... .......... 23% 89.6M 1s
 25300K .......... .......... .......... .......... .......... 23%  265M 1s
 25350K .......... .......... .......... .......... .......... 23%  107M 1s
 25400K .......... .......... .......... .......... .......... 23% 90.8M 1s
 25450K .......... .......... .......... .......... .......... 23% 72.8M 1s
 25500K .......... .......... .......... .......... .......... 23% 94.4M 1s
 25550K .......... .......... .......... .......... .......... 23%  223M 1s
 25600K .......... .......... .......... .......... .......... 23% 68.5M 1s
 25650K .......... .......... .......... .......... .......... 23%  114M 1s
 25700K .......... .......... .......... .......... .......... 23%  112M 1s
 25750K .......... .......... .......... .......... .......... 23% 85.3M 1s
 25800K ....

 45150K .......... .......... .......... .......... .......... 41% 73.2M 1s
 45200K .......... .......... .......... .......... .......... 41%  273M 1s
 45250K .......... .......... .......... .......... .......... 42% 54.5M 1s
 45300K .......... .......... .......... .......... .......... 42%  189M 1s
 45350K .......... .......... .......... .......... .......... 42% 61.7M 1s
 45400K .......... .......... .......... .......... .......... 42%  128M 1s
 45450K .......... .......... .......... .......... .......... 42%  219M 1s
 45500K .......... .......... .......... .......... .......... 42% 63.4M 1s
 45550K .......... .......... .......... .......... .......... 42% 91.2M 1s
 45600K .......... .......... .......... .......... .......... 42% 83.5M 1s
 45650K .......... .......... .......... .......... .......... 42%  231M 1s
 45700K .......... .......... .......... .......... .......... 42% 94.1M 1s
 45750K .......... .......... .......... .......... .......... 42% 90.1M 1s
 45800K ....

 65150K .......... .......... .......... .......... .......... 60%  104M 0s
 65200K .......... .......... .......... .......... .......... 60% 77.5M 0s
 65250K .......... .......... .......... .......... .......... 60%  144M 0s
 65300K .......... .......... .......... .......... .......... 60%  189M 0s
 65350K .......... .......... .......... .......... .......... 60% 72.4M 0s
 65400K .......... .......... .......... .......... .......... 60% 88.1M 0s
 65450K .......... .......... .......... .......... .......... 60% 69.0M 0s
 65500K .......... .......... .......... .......... .......... 60% 36.5M 0s
 65550K .......... .......... .......... .......... .......... 60%  188M 0s
 65600K .......... .......... .......... .......... .......... 60% 70.9M 0s
 65650K .......... .......... .......... .......... .......... 60%  134M 0s
 65700K .......... .......... .......... .......... .......... 60% 84.9M 0s
 65750K .......... .......... .......... .......... .......... 61% 70.7M 0s
 65800K ....

...

........ .......... .......... .......... 10% 47.2M 1s
  5500K .......... .......... .......... .......... .......... 10% 33.9M 1s
  5550K .......... .......... .......... .......... .......... 10%  204M 1s
  5600K .......... .......... .......... .......... .......... 10% 96.5M 1s
  5650K .......... .......... .......... .......... .......... 10%  146M 1s
  5700K .......... .......... .......... .......... .......... 10% 57.4M 1s
  5750K .......... .......... .......... .......... .......... 11% 48.1M 1s
  5800K .......... .......... .......... .......... .......... 11% 52.8M 1s
  5850K .......... .......... .......... .......... .......... 11%  103M 1s
  5900K .......... .......... .......... .......... .......... 11% 41.2M 1s
  5950K .......... .......... .......... .......... .......... 11%  215M 1s
  6000K .......... .......... .......... .......... .......... 11% 50.8M 1s
  6050K .......... .......... .......... .......... .......... 11%  267M 1s
  6100K .......... .......... ...

 18350K .......... .......... .......... .......... .......... 35% 57.5M 1s
 18400K .......... .......... .......... .......... .......... 35%  234M 1s
 18450K .......... .......... .......... .......... .......... 35% 15.8M 1s
 18500K .......... .......... .......... .......... .......... 35%  129M 1s
 18550K .......... .......... .......... .......... .......... 35% 63.2M 1s
 18600K .......... .......... .......... .......... .......... 35%  207M 1s
 18650K .......... .......... .......... .......... .......... 35% 62.1M 1s
 18700K .......... .......... .......... .......... .......... 35% 45.1M 1s
 18750K .......... .......... .......... .......... .......... 35% 80.5M 1s
 18800K .......... .......... .......... .......... .......... 35% 69.5M 1s
 18850K .......... .......... .......... .......... .......... 36%  206M 1s
 18900K .......... .......... .......... .......... .......... 36% 79.5M 1s
 18950K .......... .......... .......... .......... .......... 36% 51.9M 1s
 19000K ....

 32300K .......... .......... .......... .......... .......... 61% 71.2M 0s
 32350K .......... .......... .......... .......... .......... 61%  255M 0s
 32400K .......... .......... .......... .......... .......... 61% 88.3M 0s
 32450K .......... .......... .......... .......... .......... 62% 56.8M 0s
 32500K .......... .......... .......... .......... .......... 62% 89.4M 0s
 32550K .......... .......... .......... .......... .......... 62% 62.9M 0s
 32600K .......... .......... .......... .......... .......... 62%  113M 0s
 32650K .......... .......... .......... .......... .......... 62% 49.8M 0s
 32700K .......... .......... .......... .......... .......... 62% 20.3M 0s
 32750K .......... .......... .......... .......... .......... 62% 26.4M 0s
 32800K .......... .......... .......... .......... .......... 62%  117M 0s
 32850K .......... .......... .......... .......... .......... 62%  231M 0s
 32900K .......... .......... .......... .......... .......... 62%  101M 0s
 32950K ....

 45700K .......... .......... .......... .......... .......... 87% 27.1M 0s
 45750K .......... .......... .......... .......... .......... 87% 68.2M 0s
 45800K .......... .......... .......... .......... .......... 87% 57.5M 0s
 45850K .......... .......... .......... .......... .......... 87%  203M 0s
 45900K .......... .......... .......... .......... .......... 87% 80.4M 0s
 45950K .......... .......... .......... .......... .......... 87% 56.8M 0s
 46000K .......... .......... .......... .......... .......... 87% 69.4M 0s
 46050K .......... .......... .......... .......... .......... 88%  183M 0s
 46100K .......... .......... .......... .......... .......... 88% 55.6M 0s
 46150K .......... .......... .......... .......... .......... 88% 68.1M 0s
 46200K .......... .......... .......... .......... .......... 88% 55.4M 0s
 46250K .......... .......... .......... .......... .......... 88% 45.6M 0s
 46300K .......... .......... .......... .......... .......... 88%  220M 0s
 46350K ....

2023-04-21 23:57:25 (59.9 MB/s) - ‘/home/sk9944_nyu_edu/TAXI/YELLOW_CABS/yellow_tripdata_2022-12.parquet’ saved [53640739/53640739]



In [5]:
# downloading Green cab data(2019-2022) from site https://www.nyc.gov/site/tlc/about/tlc-trip-record-data.page
url = "https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_20"
output_dir = "/home/sk9944_nyu_edu/TAXI/GREEN_CABS/"
for i in range(19,23):
    for j in range(1, 13):
        url_1 = str(j)
        if j<10:
            url_1 = "0"+url_1
        print("wget "+ url+str(i)+"-"+url_1+".parquet")
        # Run wget command
        subprocess.call(["wget", "-P", output_dir, url+str(i)+"-"+url_1+".parquet"])

--2023-04-21 23:57:25--  https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2019-01.parquet
Resolving d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)... 13.249.90.174, 13.249.90.181, 13.249.90.176, ...
Connecting to d37ci6vzurychx.cloudfront.net (d37ci6vzurychx.cloudfront.net)|13.249.90.174|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 11071980 (11M) [binary/octet-stream]
Saving to: ‘/home/sk9944_nyu_edu/TAXI/GREEN_CABS/green_tripdata_2019-01.parquet’

     0K .......... .......... .......... .......... ..........  0% 4.51M 2s
    50K .......... .......... .......... .......... ..........  0% 4.80M 2s
   100K .......... .......... .......... .......... ..........  1% 8.05M 2s
   150K .......... .......... .......... .......... ..........  1% 11.7M 2s
   200K .......... .......... .......... .......... ..........  2% 13.8M 1s
   250K .......... .......... .......... .......... ..........  2% 20.3M 1s
   300K .......... .......... ...

wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2019-01.parquet


. 25%  199M 0s
  2750K .......... .......... .......... .......... .......... 25% 45.2M 0s
  2800K .......... .......... .......... .......... .......... 26%  221M 0s
  2850K .......... .......... .......... .......... .......... 26%  312M 0s
  2900K .......... .......... .......... .......... .......... 27%  256M 0s
  2950K .......... .......... .......... .......... .......... 27%  236M 0s
  3000K .......... .......... .......... .......... .......... 28%  250M 0s
  3050K .......... .......... .......... .......... .......... 28% 38.0M 0s
  3100K .......... .......... .......... .......... .......... 29%  229M 0s
  3150K .......... .......... .......... .......... .......... 29%  346M 0s
  3200K .......... .......... .......... .......... .......... 30%  222M 0s
  3250K .......... .......... .......... .......... .......... 30% 63.1M 0s
  3300K .......... .......... .......... .......... .......... 30% 58.6M 0s
  3350K .......... .......... .......... .......... .......... 31% 38.1M 

Saving to: ‘/home/sk9944_nyu_edu/TAXI/GREEN_CABS/green_tripdata_2019-02.parquet’

     0K .......... .......... .......... .......... ..........  0% 4.17M 2s
    50K .......... .......... .......... .......... ..........  0% 5.11M 2s
   100K .......... .......... .......... .......... ..........  1% 9.66M 2s
   150K .......... .......... ......

wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2019-02.parquet


...

HTTP request sent, awaiting response... 200 OK
Length: 1312353 (1.3M) [binary/octet-stream]
Saving to: ‘/home/sk9944_nyu_edu/TAXI/GREEN_CABS/green_tripdata_2022-07.parquet’

     0K .......... .......... .......... .......... ..........  3% 3.90M 0s
    50K .......... .......... .......... .......... ..........  7% 4.86M 0s
   100K .......... .......... .......... .......... .......... 11% 9.38M 0s
   150K .......... .......... .......... .......... .......... 15% 11.2M 0s
   200K .......... .......... .......... .......... .......... 19% 12.8M 0s
   250K .......... .......... .......... .......... .......... 23% 15.6M 0s
   300K .......... .......... .......... .......... .......... 27% 17.7M 0s
   350K .......... .......... .......... .......... .......... 31% 13.7M 0s
   400K .......... .......... .......... .......... .......... 35% 21.3M 0s
   450K .......... .......... .......... .......... .......... 39% 32.2M 0s
   500K .......... .......... .......... .......... .......... 42%

wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2022-09.parquet
wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2022-10.parquet


Saving to: ‘/home/sk9944_nyu_edu/TAXI/GREEN_CABS/green_tripdata_2022-09.parquet’

     0K .......... .......... .......... .......... ..........  3% 4.17M 0s
    50K .......... .......... .......... .......... ..........  7% 5.07M 0s
   100K .......... .......... .......... .......... .......... 10% 9.46M 0s
   150K .......... .......... .......... .......... .......... 14% 10.4M 0s
   200K .......... .......... .......... .......... .......... 17% 14.6M 0s
   250K .......... .......... .......... .......... .......... 21% 16.9M 0s
   300K .......... .......... .......... .......... .......... 24% 19.8M 0s
   350K .......... .......... .......... .......... .......... 28% 19.2M 0s
   400K .......... .......... .......... .......... .......... 31% 24.7M 0s
   450K .......... .......... .......... .......... .......... 35% 20.0M 0s
   500K .......... .......... .......... .......... .......... 38% 51.0M 0s
   550K .......... .......... .......... .......... .......... 42% 28.7M 0s
   600

wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2022-11.parquet
wget https://d37ci6vzurychx.cloudfront.net/trip-data/green_tripdata_2022-12.parquet


....... 12% 16.9M 0s
   150K .......... .......... .......... .......... .......... 16% 13.2M 0s
   200K .......... .......... .......... .......... .......... 20% 13.2M 0s
   250K .......... .......... .......... .......... .......... 24% 21.8M 0s
   300K .......... .......... .......... .......... .......... 28% 19.3M 0s
   350K .......... .......... .......... .......... .......... 32% 17.6M 0s
   400K .......... .......... .......... .......... .......... 36% 27.6M 0s
   450K .......... .......... .......... .......... .......... 40% 35.1M 0s
   500K .......... .......... .......... .......... .......... 44% 37.1M 0s
   550K .......... .......... .......... .......... .......... 48% 57.2M 0s
   600K .......... .......... .......... .......... .......... 52% 34.0M 0s
   650K .......... .......... .......... .......... .......... 56% 55.6M 0s
   700K .......... .......... .......... .......... .......... 60% 36.7M 0s
   750K .......... .......... .......... .......... .......... 64% 

In [6]:
local_directory_path = "/home/sk9944_nyu_edu/TAXI/"

# HDFS directory to copy the directory to
hdfs_directory_path = "/shared/TAXI"
hdfs_shared_path = "/shared/"

subprocess.call(["hdfs", "dfs", "-rm", "-r", hdfs_directory_path])

Deleted /shared/TAXI


0

In [7]:
subprocess.call(["hdfs", "dfs", "-put", local_directory_path, hdfs_shared_path])

0

23/04/22 00:01:32 WARN org.apache.spark.scheduler.cluster.YarnSchedulerBackend$YarnSchedulerEndpoint: Requesting driver to remove executor 1 for reason Container marked as failed: container_e02_1679692348553_20916_01_000003 on host: nyu-dataproc-sw-q29v.c.hpc-dataproc-19b8.internal. Exit status: -100. Diagnostics: Container released on a *lost* node.
23/04/22 00:01:32 ERROR org.apache.spark.scheduler.cluster.YarnScheduler: Lost executor 1 on nyu-dataproc-sw-q29v.c.hpc-dataproc-19b8.internal: Container marked as failed: container_e02_1679692348553_20916_01_000003 on host: nyu-dataproc-sw-q29v.c.hpc-dataproc-19b8.internal. Exit status: -100. Diagnostics: Container released on a *lost* node.


In [ ]:
subprocess.call(["rm", "-rf", "-put", local_directory_path, hdfs_shared_path])